# Recherche de motif dans un texte

Ce TP étudie un algorithme particulièrement efficace pour rechercher une sous-chaîne (le motif) dans une chaîne (le texte).
On dispose donc d'une grande chaîne de caractères $t_0t_1t_2\dots t_{N - 1}$, de longueur $N$, et d'un mot plus court de longueur $n$, noté $x_0x_1x_2\dots x_{n - 1}$. On cherche l'indice (ou les indices) auquel apparaît le motif.    
_Exemple_ : le motif _abaa_ apparaît dans le texte _acaabbabaaa_ à la position 6.  

## Algorithme naïf
On compare le motif à une _fenêtre_ glissante dans le texte, c'est-à-dire à un groupe de lettres de même longueur que le motif. Pour préparer à l'algorithme de Boyer-Moore, on effectue la comparaison de droite à gauche (et non de gauche à droite comme on le ferai habituellement). 
Implémenter l'algorithme suivant :   
   
__Données__ :  
Un texte _t_ de longueur $N$  
Un motif _x_ de longueur $n \geq N$   
__Renvoie__ :  
Toutes les positions de _x_ dans _t_    
> _P_ $\leftarrow$ liste vide # liste des positions  
> __pour__ _i_ de 0 à $N - n + 1$ (de 0 à $N - n$ inclus):    
>> _j_ $\leftarrow$ $n - 1$   
>> __Tant que__ _j_ $\geq$ 0 et $x_j = t_{i + j}$ :  
>>> _j_ $\leftarrow$ j - 1  

>> __si__ _j_ = -1 : 
>>> Ajouter _i_ à _P_

> Renvoyer _P_   

[comment]: <> (_REMARQUE_ : peut-être une erreur à voir si le motif est en position 0)


In [ ]:
def rechercheNaive(texte, motif):
    """
    Renvoie les positions d'un motif dans un texte
    @param texte, motif : chaine de caractères. La longueur N de texte est ≥ à celle de motif
    @return positions : liste des positions du motif dans le texte
    @return compteur : facultatif, compte les comparaisons
    """
    positions = []
    n = len(motif)
    N = len(texte)
    compteur = 0
    assert N >= n, "le texte doit être plus long que le motif"
        
    return positions, compteur

def testsNaifs(couples):    
    for element in couples:
        print("Motif : ",element[0], "texte : ", element[1])
        print("résultats",rechercheNaive(element[1], element[0]), "\n")

couples = [("abaa", "acaabbabaaa"),
           ("aaaa", "aaaaaaaaaaa"),
           ("caaa","aaaaaaaaaaa"),
          ("pilotes", "les pecheurs rudoyes de cet ouest battu des vents font des pilotes habiles")]
testsNaifs(couples)

On reprend l'exemple précédent ( motif _abaa_ , texte _acaabbabaaa_ ). Le tableau ci-dessous donne le déroulement de l'algorithme, le caractère en gras donnant la première lettre du motif où la différence est repérée (en partant de la droite).  

|_i_|a|  c  |a|a|  b  |  b  |a|  b  |  a  |a|a|
|---|-|-----|-|-|-----|-----|-|-----|-----|-|-|
| 0 |a|__b__|a|a|     |     | |     |     | | |
| 1 | |  a  |b|a|__a__|     | |     |     | | |
| 2 | |     |a|b|  a  |__a__| |     |     | | |
| 3 | |     | |a|  b  |__a__|a|     |     | | |
| 4 | |     | | |  a  |  b  |a|__a__|     | | |
| 5 | |     | | |     |  a  |b|__a__|  a  | | |
| 6 | |     | | |     |     |a|  b  |  a  |a| |
| 7 | |     | | |     |     | |  a  |__b__|a|a|


Compter le nombre de comparaisons dans les cas suivants:
* motif _aaa_ , texte _aaaaaaaaaaa_
* motif _caaa_ , texte _aaaaaaaa_  

Donner la complexité de l'algorithme naïf en fonction de _n_ et _N_.

## Règle du mauvais caractère
Reprenons le tableau précédent. On peut constater que la deuxième lettre du texte est _c_, qui n'apparaît pas dans le motif. Il est donc inutile de tester le cas _i_ = 1 puisque motif et texte différeront au moins sur cette lettre. Pour _i_ = 2, la différence est constatée en comparant le dernier _b_ de la fenêtre, dans le texte, avec le dernier _a_ du motif. On peut donc chercher directement à aligner le _b_ de la fenêtre avec un _b_ du motif : on passe directement à _i_ = 4. De la même manière, expliquer pourquoi on saute l'étape _i_ = 5.  
  
|_i_|a|  c  |a|a|b|  b  |a|  b  |  a  |a|a|
|---|-|---- |-|-|-|-----|-|-----|-----|-|-|
| 0 |a|__b__|a|a| |     | |     |     | | |
| 2 | |     |a|b|a|__a__| |     |     | | |
| 4 | |     | | |a|  b  |a|__a__|     | | |
| 6 | |     | | | |     |a|  b  |  a  |a| |
| 7 | |     | | | |     | |  a  |__b__|a|a|

### Programmation effective : l'algorithme de Boyer-Moore simplifié (Horspool)

Pour implémenter la règle du mauvais caractère, on va créer un tableau associatif (un dictionnaire), dont les clés sont les lettres du motif, et les valeurs la dernière position de la lettre dans le motif, sauf pour la dernière lettre. Ce dictionnaire permettra de calculer directement le décalage de la fenêtre dans le mot à explorer.
Ecrire la fonction `lettreADroite(motif)` qui renvoie ce dictionnaire.
_Exemple_ : `lettreADroite('exercice')` renvoie `pos_droite = {'e':7, 'c':6, 'i':5, 'r':3, 'x':1}`.

In [ ]:
def lettreADroite(motif):
    pos_droite = {}

    return pos_droite

def testsPosDroite(couples):
    for element in couples:
        print("Avec le motif ", element[0], "on obtient ",lettreADroite(element[0]))

testsPosDroite(couples)

On modifie l'algorithme précédent pour qu'il prenne en compte la règle du mauvais caractère. La boucle __pour__ est remplacée par un __tant que__. Si le motif ne correspond pas à la fenêtre, alors le décalage est calculé en tenant compte du dictionnaire des positions. On tient aussi compte du fait qu'une lettre du texte peut ne pas être dans le motif, la clé correspondante est donc absente du dictionnaire. 
Compléter l'algorithme suivant, en donnant l'instruction qui permet de calculer _i_ (remarque : la solution est en commentaire, visible en double cliquant dans cette cellule).
  
   
__Données__ :  
Un texte _t_ de longueur $N$  
Un motif _x_ de longueur $n \geq N$   
Le dictionnaire _pos\_droite_ donnant la dernière position de tous les caractères du motif (dernière lettre exceptée)   
__Renvoie__ :  
Toutes les positions de _x_ dans _t_    
> _P_ $\leftarrow$ liste vide # liste des positions   
> _i_ $\leftarrow$ 0   
> __Tant que__ _i_ ≤ $N - n$ :    
>> _j_ $\leftarrow$ $n - 1$   
>> __Tant que__ _j_ $\geq$ 0 et $x_j = t_{i + j}$ :  
>>> _j_ $\leftarrow$ j - 1   

>> __si__ _j_ = -1 :  

>>> Ajouter _i_ à _P_   

>> _i_ $\leftarrow$ ...<!--_i_ + max(1, _j_ - _pos\_droite_$[t_{i + j}]$) si la lettre existe dans le motif-->

> Renvoyer _P_   
  
  
Implémenter cet algorithme. Pour tenir compte du fait que le dictionnaire des positions des lettres du motif ne contient pas forcément toutes les lettres du texte, on pourra créer une fonction supplémentaire `droite(c)` qui renvoie la valeur correspondante si la clé existe, et -1 sinon.

In [ ]:
def droite(c, pos_droite):
    if c in pos_droite.keys():
        return pos_droite[c]
    else:
        return -1

def horspool(texte, motif, pos_droite):
    """
    Renvoie les positions d'un motif dans un texte
    @param texte, motif : chaine de caractères. La longueur N de texte est ≥ à celle de mtof
    @return positions : liste des positions du motif dans le texte
    @return compteur : facultatif, compte les comparaisons
    """
    positions = []
    n = len(motif)
    N = len(texte)
    assert N >= n, "le texte doit être plus long que le motif"
    compteur = 0
    
    return positions, compteur

def tests_horspool(couples):    
    for element in couples:
        pos_droite = lettreADroite(element[0])
        print("Motif : ",element[0], "texte : ", element[1], "dictionnaire :",pos_droite)
        print("résultats", horspool(element[1], element[0], pos_droite), "\n")

couples = [("abaa", "acaabbabaaa"),
           ("aaaa", "aaaaaaaaaaa"),
           ("caaa","aaaaaaaaaaa"),
          ("pilotes", "les pecheurs rudoyes de cet ouest battu des vents font des pilotes habiles")]

tests_horspool(couples)

On peut constater que cette amélioration ne change pas la complexité théorique. En pratique, il y a amélioration effective. Ceci est d'autant plus vrai avec la version suivante, qui est un approfondissement, assez complexe.

## Algorithme de Boyer-Moore
_Pour ceux qui sont en avance ou qui souhaitent approfondir_

### Règle du bon suffixe
_Exemple_ : on cherche le motif _x = abaaaa_ dans le texte _t = abbcaacaaaabaaaa_ (il est à la fin, en position 10).  
  
Pour `i = 0`, la fenêtre est abbcaa. Le "bon suffixe" est obtenu en partant de la droite. C'est la partie de la fenêtre commune avec une partie du motif. Ici c'est _aa_ : _x = abaa_ __aa__ et _t = abbc_ __aa__ _caaaabaaaa_. On va décaler la fenêtre pour aligner ce suffixe avec une copie de aa entre texte et suffixe. On pourrait décaler de 1, en se basant sur x = _aba_ __aa__ _a_ . Dans ce cas, on constate que cette copie est précédée d'un _a_. Or c'était déjà le cas pour le "bon suffixe" : on va donc reproduire la même erreur. Par contre, si on décale de 2, en se basant sur _x = ab_ __aa__ _aa_ , la lettre précédente est _b_ , différente du _a_ précédant le "bon suffixe". La décalage est donc pertinent, la comparaison de la lettre précédant le "bon suffixe" étant différente.  
  
On se place donc en `i = 2`, la fenêtre est _bcaaca_. Le "bon suffixe est" _a_. Sa copie dans le motif qui n'est pas précédée d'un _a_ est en position 2 : _ab_ __a__ _aaa_. On décale le motif pour aligner ce _a_ avec le dernier _a_ de la fenêtre (soit `i = 5`).  
  
On est donc en `i = 5`, on compare le motif _abaaaa_ avec la fenêtre _acaaaa_. La "bon suffixe" est _aaaa_. Il n'apparaît pas ailleurs dans le motif, on ne peut pas appliquer la méthode précédente (pour passer de `i = 0`à `i = 2`puis `i = 5`). On va utiliser une règle différente : on va chercher le préfixe du motif _x_ le plus long possible, qui soit aussi suffixe du "bon suffixe" (ça suit au fond ?). Ici c'est _a_ car :  
* le bon suffixe finit par _a_ , et x commence par _a_
* x commence par _ab_ mais le bon suffixe ne commence pas par _ab_  
On aligne ce préfixe du motif _x_ avec le suffixe correspondant du bon suffixe. Le décalage est donc de 5 lettres, on passe à `i = 10`.
   
   
|_i_|a|b|b|  c  |a|a|  c  |a|a|a|a|b|a|a|a|a|
|---|-|-|-|-----|-|-|-----|-|-|-|-|-|-|-|-|-|
| 0 |a|b|a|__a__|a|a|     | | | | | | | | | |
| 2 | | |a|  b  |a|a|__a__|a| | | | | | | | |
| 5 | | | |     | |a|__b__|a|a|a|a| | | | | |
| 10| | | |     | | |     | | | |a|b|a|a|a|a|


_Remarque_ : calculer ce décalage en temps linéaire n'est pas trivial. On ne se posera pas ce problème dans le cadre de ce TP.

### Algorithme final
Dans l'algorithme final, on applique le meilleur des deux décalages obtenus avec la règle du mauvais caractère, et la règle du bon suffixe. 

_Exercice_ : appliquer l'algorithme final à:
1. motif = _abaaaa_ , texte = _abbcaacaaaabaaaa_
2. texte = _GCATCGCAGAGAGTATACAGTACG_ , motif _GCAGAGAG_
3. texte = _aabbbababacaabbaba_ , motif _aababab_
4. motif = _abacab_ , texte = _abacaabadcabacabaabb_
5. texte = _CBADBCACBADCBBACACBCAABCA_ , motif = _CBCAABCA_
 



### Programmation de l'algorithme
On modifie l'algorithme initial.  
  
  
__Données__ :  
Un texte _t_ de longueur $N$.  
Un motif _x_ de longueur $n \geq N$.   
Le dictionnaire _pos\_droite_ donnant la dernière position de tous les caractères du motif.  
Deux tableaux _s_ et _p_ tels que :
* _s_ est le tableau des bon suffixes. $s[j] = s_x(j)$, où $s_x(j)$ est la position la plus à droite d'une copie du suffixe $x_{[j,m[}$, formé des dernières lettres de _x_ à partir de la j-ième. Cette copie ne doit pas être précédée de la lettre d'indice _j - 1_ de _x_. Si une telle copie n'existe pas, alors $s[j] = -1$.
* _p_ est le tableau des préfixes. $p[j] = p_x(j)$, où $p_x(j)$ est la longueur du plus long préfixe de _x_ qui soit aussi suffixe de $x_{[j,m[}$. On impose que le préfixe soit différent de _x_ entier, on pose donc $p[0] = p[1]$.
  
__Renvoie__ :  
Toutes les positions de _x_ dans _t_    
>_P_ $\leftarrow$ liste vide # liste des positions   
>_i_ $\leftarrow$ 0   
>__Tant que__ _i_ ≤ $N - n$ :    
>>_j_ $\leftarrow$ $n - 1$   
>>__Tant que__ _j_ $\geq$ 0 et $x_j = t_{i + j}$ :  
>>>_j_ $\leftarrow$ j - 1   
  
>>__si__ _j_ = -1 :  

>>>Ajouter _i_ à _P_   
>>>i  $\leftarrow$ i + _n_ - _p_[1]  
  
>>__Sinon__ :

>>>__SI__ _s_\[ _j_ + 1\] ≥ 0 : _i_ $\leftarrow$ _i_ + max(_j_ - _pos\_droite_ $[t_{i + j}]$ , j + 1 - _s_\[ _j_ + 1\])  
>>>__Sinon__ : _i_ $\leftarrow$ _i_ + max(n - _p_\[ _j_ \] , _j_ - _pos\_droite_ $[t_{i + j}]$)

>Renvoyer _P_  
  
Ecrire les fonctions donnant les tableaux _s_ et _p_, puis implémenter l'algorithme.   
On peut le tester avec les fichiers chr18 (chromosome 18). Tests rapides : chr18_3 ou chr18_4 dans chr_2, assez rapide : chr18_2 dans chr18_0. Plus long : chr18_3 dans chr_0. Pour ouvrir les fichiers et les sauver , vous pouvez reprendre la fonction ci-dessous. On peut rajouter un compteur dans le programme pour le nombre de comparaisons, et constater que l'on gagne beaucoup en efficacité par rapport à la méthode naïve.

In [ ]:
def BoyerMoore(texte, motif):
    return

def test():
    C = []
    for i in range(5):
        with open(f'chr18/chr18_{i}') as c:
            C.append(c.read().replace('\n',''))

    for i in range(len(C)):
        print("longueur de chr18_",i,":",len(C[i]))
            
    print("Test de l'algorithme pour chercher chr18_3 dans chr18_0 :")
    print(BoyerMoore(C[0], C[3]))

<hr style="color:black; height:1px />
<div style="float:left;margin:0 10px 10px 0" markdown="1" style = "font-size = "x-small">
<a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/4.0/"><img alt="Licence Creative Commons" style="border-width:0" src="https://i.creativecommons.org/l/by-nc-sa/4.0/88x31.png" /></a><br />Ce(tte) œuvre est mise à disposition selon les termes de la <a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/4.0/">Licence Creative Commons Attribution - Pas d’Utilisation Commerciale - Partage dans les Mêmes Conditions 4.0 International</a>.     
  
Un grand merci à Bruno Grenet, Université de Montpellier II, source principale de ce TD.  
Voir aussi [ici](https://www-igm.univ-mlv.fr/~lecroq/string/examples/exp14.html) pour un des exercices avec le détail des décalages.

frederic.mandon`@`ac-montpellier.fr, Lycée Jean Jaurès - Saint Clément de Rivière - France<br></div> 